In [1]:
!pip install scqubits;


[notice] A new release of pip is available: 23.1.2 -> 23.2.1
[notice] To update, run: python3.11 -m pip install --upgrade pip


# U.S. QIS Summer School 2023

## Track 3:  Modeling superconducting qubits with `scqubits` & `qutip`

Ziwen Huang (Fermilab)<br>
Xinyuan You (Fermilab)<br>
Jens Koch (Northwestern)


<br>

### OVERALL GOAL

Simulate a $X_\pi$ gate on a transmon. The model system we consider consists of a transmon coupled capacitively to a resonator. The system will be operated in the dispersive regime and the gate will be implemented by means of a microwave tone acting on the resonator.

(We will make this problem fully specific as we go along.)

As part of this session, we will be using Python along with four open-source packages: `scqubits`, `qutip`, `numpy` and `matplotlib`. If you are encountering Python for the first time in your life: it's one of the easiest programming languages to learn. If all is brand new for you today, you may not understand every nuance yet, but you will get a good first swimming lesson with assistance and guidance.

**RESOURCES**:
* `matplotlib` cheatsheats:  https://matplotlib.org/cheatsheets/
* `scqubits` documentation:  https://scqubits.readthedocs.io/en/v3.2/index.html
* `numpy` cheatsheats:       https://tinyurl.com/npycheat
* `qutip` documentation:     https://qutip.org/docs/latest/


<br>

### Task 1

Use the `scqubits` GUI to select appropriate transmon parameters. We would like a transmon qubit with a **01 frequency close to 6 GHz**. Fire up the GUI, pick a charging energy of 0.2 GHz and adjust the Josephson energy to hit the desired qubit frequency. What is your resulting $E_J/E_C$ ratio?

[answer: $E_J$$\approx$24 GHz should get you close; resulting in $E_J/E_C$$\approx$120.

*Advanced*:<br>
use `Transmon.find_EJ_EC(...)` for automatic and precision solutions. Suppose we are aiming for $\omega_{01}/2\pi$=6 GHz and an anharmonicity of -0.2 GHz. What should we pick for charging and Josephson energies?
[answer: $E_J$$\approx$ 25.8 GHz, $E_C$$\approx$ 0.185 GHz



### Task 2

Ultimately, the $X_\pi$ gate we wish to implement is enabled by driving Rabi oscillations among the 0 and 1 levels of the transmon. When coupling the transmon capacitively, it is the charge operator $\hat{n}$ that is driven, and relevant transition matrix elements have the form $|\langle 0 | \hat{n} | 1\rangle|$. Use the GUI to compare the magnitude of charge matrix elements for 0$\to$1 vs. 0$\to$ higher levels. Can you understand the behavior?

There are different ways of approaching this question. You can inspect wavefunctions & their parity. You can also resort to the approximate transmon model based on the Kerr oscillator model, $\hat{H}=\hbar\omega_{01} \hat{b}^\dagger \hat{b} - \tfrac{1}{2}\alpha \hat{b}^\dagger\hat{b}(\hat{b}^\dagger\hat{b}-1)$ and think about how the charge operator $\hat{n}$ relates to the creation and annihilation operators $\hat{b}^\dagger, \hat{b}$.

*Advanced*:<br>
Are the observed selection rules a general result for superconducting qubits? Check out the charge matrix elements of the fluxonium qubit, both at zero and non zero flux. Again, inspection of the wavefunctions is revealing. What about a story based on $\hat{b}$ and $\hat{b}^\dagger$?

### Task 3

Create an instance of the transmon qubit, either by `tmon = scq.Transmon.create()` or by `tmon = scq.Transmon(EJ=,...)`. Obtain the energy eigenvalues via `tmon.eigenvals()`. What is your transmon's 01 frequency?

*Basic*:<br>

- If you are relatively new to numpy, Python, coding in general: familiarize yourself with `numpy` arrays. `evals = tmon.eigenvals()` is a 1d numpy array with float-valued entries, i.e. collection of real numbers as in a vector.
- You can access individual elements by their indices. The first element has index 0:
`evals[0]`.
- Access the first two elements to compute the 01 transition frequency.
- What do `evals[-1]` and `evals[-2]` produce?
- How about `evals[1:3]`?

*Medium*:<br>

The transmon energies are designed to be insensitive to the offset charge `ng`. - Obtain eigenergies or visualize the spectrum as a function of this parameter.
-  Define the range of values of `ng` via `ngvals = np.linspace(<start>, <stop>, <number of points>)` and then use `tmon.get_evals_vs_paramvals(...)` or `tmon.plot_evals_vs_paramvals(...)`.
- What do you observe for energy variations vs. `ng`?
- What happens if you considerably lower the Josephson energy via `tmon.EJ = <new value>`?

*Advanced*:<br>
- Show: any approximation to the transmon problem in which periodic boundary conditions are substituted by $\lim_{\varphi\to\pm\infty} \psi(\varphi) = 0$ cannot capture the influence of the offset charge. (Hint: there is a simple function $f$ such that the gauge transformation $\bar{\psi} = \psi\, e^{i f(n_g)}$  completely eliminates $n_g$ from the approximated problem once the boundary conditions are replaced.)
- What does offset charge dependence of energy levels look like in the Cooper pair box regime where $E_J<E_C$? What can you learn from a perturbative treatment of the entire potential energy term?

<br>

### Task 4

Driving the transmon directly (i.e., coupling a drive line to the transmon via a direct coupling capacitor) is generally a bad idea for qubit coherence. Nonetheless, it is instructive to explore this case from a conceptual standpoint. (The usual mode of operation by indirectly driving the transmon via a resonator actually ends up looking quite similar after some simplifications.)

So suppose our full Hamiltonian now includes both the transmon and a drive $\hat{H} = \hat{H}_\text{tmon} + \hat{H}_\text{drive}(t)$, where

$$\hat{H}_\text{drive}(t) = \epsilon(t) \cos(\omega_d t)\, \hat{n},$$

where $\omega_d$ is the drive frequency (or carrier frequency) and $\epsilon(t)$ is an envelope function by which we form a pulse of finite duration. This could be a Gaussian, or a rectangular-window function, etc.

Simulating quantum mechanical time evolution is a top strength of the `qutip` package. The specific function responsible for solving the time-dependent Schrodinger equation is `qutip`'s `sesolve`: https://qutip.org/docs/latest/guide/dynamics/dynamics-time.html

Employing an adaptive step size ODE solver, `sesolve` solves the initial value problem posed by the time-dependent Schrodinger equation
$$i\hbar \frac{d}{dt} |\psi(t)\rangle = \bigg(H_\text{tmon} + H_\text{drive}(t)\bigg)|\psi(t)\rangle$$
when accompanied by some initial state $|\psi(t=0)\rangle = |\psi_0\rangle$. As a first attempt, we will simply "stuff" our entire Hamiltonian into `sesolve`, using the most efficient method offered by `qutip`: the string-based mode in which Cython is invoked behind the scenes to accelerate the computation.

For the window function $\epsilon(t)$, there is a variety of popular choices https://en.wikipedia.org/wiki/Window_function, and the choice will generally affect the fidelity of the gate. Maximizing fidelity is an important goal in its own right, but not our main focus right now. So we will opt for a simple window function that smoothly switches the pulse on and off for a pulse duration $\tau_p$:

$$ \epsilon(t) = A \, \sin^2 (\pi t/\tau_p) $$

This is called a **Hann window** (named after Austrian meteorologist Julius von Hann). Sketch this function (or plot it, if you like) to confirm that it "does the job": it smoothly switches on at $t=0$ and off at $t=\tau_p$.

In string-based mode, `sesolve` has the following syntax:

`q.sesolve(ham_list, psi0, times, observables, args=args)`

where the individual (keyword) arguments are:
- `ham_list = [H_static, [drive_op, 'A * sin(pi * t / tau_p)**2 * cos(omega_d * t)']]` <br> Here, `H_static = tmon.hamiltonian()` is the transmon hamiltonian, `drive_op = tmon.n_operator()` is the charge number operator $\hat{n}$ and the c-number function multiplying the drive operator is provided in string form. (It is for this piece that `qutip` invokes Cython and performs compilation behind the scenes.)
- `psi0` is our initial state, for simplicity, let us pick the transmon ground state. Qutip requires this input in its special `Qobj` format, but that's easily achieved:<br> `_, evecs = tmon.eigensys()`<br>`zero_state = q.Qobj(evecs[:, 0])` <br> `psi0 = zero_state`
- `times` is a list of times which fulfills two roles: (1) the first and last elements `times[0]` and `times[-1]` fix the total time interval over which `sesolve` performs time evolution; (2) `times` represents the time grid on which the expectation values of desired observables are saved. (Note: `times` does NOT set the step size for the ODE solver! That step size is chosen adaptively.)
- `observables` is a list of operators (of qutip kind) for which the expectation values are are computed at each time instance given by `times`. We are interested in occupation probabilities of states $|0\rangle$ and $|1\rangle$, which can be understood as expectation values of the projection operators onto the two states: $$p_0 = \langle |0\rangle\langle 0| \rangle_t = \langle \psi(t) | 0 \rangle \langle 0 | \psi(t) \rangle = |\langle \psi(t) | 0\rangle |^2$$ and similarly for state $|1\rangle$. Thus, defining `one_state = q.Qobj(evecs[:, 1])`, we use<br> `observables = [zero_state * zero_state.bra(), one_state * one_state.bra()]`.
- Finally, the `args` keyword argument accepts a Python dictionary that specifies free parameters in the string-based expression and the values that should be assigned to them <br>
```
A = 0.07       # max. amplitude of drive tone
tau_p = 10.0   # try pulse duration of 10 ns, still have to adjust
args = {
    'A': A,                        # amplitude in GHz
    'tau_p': tau_p,                # pulse duration in ns
    'omega_d': 2 * np.pi * E_01    # ang. drive frequency on resonance with 01
    }
```


The solution object that qutip hands back as a result of the call
`sol = q.sesolve(ham_list, psi0, times, observables, args=args)` contains the expectation values: `sol.expect[0]` and `sol.expect[1]` are `numpy` arrays with the computed expectation values of our two observables.

*Basic*:
- Following the steps outlined above, use `sesolve` to simulate the evolution under the influence of a resonant drive with a Hann window envelope. Start your qubit in the 0 or 1 state and compute the occupation probabilities for states 0 and 1.
- Use `matplotlib` to plot the results: `plt.plot(times, sol.expect[0])` and similarly for `sol.expect[1]`. You can plot both curves simultaneously by combining two calls to `plot` in the same jupyter cell.
- Play with pulse duration and/or amplitude. What do you observe?
- What would you do to create an $X_\pi$ gate?

*Medium*:
- The rotation angle is related to the area under the envelope. Recall (or work out once more) how this works when Rabi driving a two-level system on resonance.
- Based on this, make your best "guess" for the optimal pulse duration.
- Do the occupation probabilities for the $|0\rangle$ and $|1\rangle$ states add up to 1? Explain!
- If you find discrepancies: visualize where any missing probability amplitude might have gone.

*Advanced*:
- Once done with the above, consider making this computation more efficient by going into a frame co-rotating with the drive and using RWA. What is the effective Hamiltonian in that case?
- Consider the problem of leakage more systematically. What factors play a role? Consider quantities including $E_J/E_C$, $A$, $\tau_p$, etc.


### Task 5

More realistic modeling of transmon qubits and their use in today's (mini-)quantum processors: typically, transmon's are not driven directly, but indirectly via an oscillator mode of a lumped LC oscillator, a 2d resonator, or a 3d cavity.

In `scqubits`, we can create composite systems with the `HilbertSpace` class. This class takes care of several things:
- it collects information about the subsystems involved
- we can add interactions among subsystems
- it can generate a lookup table that allows us, in the dispersive regime, to go back and forth between labeling states in the bare product basis, and simple indexing of the dressed states.

*Basic*:<br>
- Create a `HilbertSpace` object composed of the transmon (already in place) and an `Oscillator` with frequency 7.5 GHz.
- You can get the Hamiltonian and eigenenergies of the combined system (yet, no interaction yet), by `<HilbertSpace>.hamiltonian()` and `<HilbertSpace>.eigenvals()`. Take a look and make sure you understand. (This is all about how two Hilbert spaces get combined into a new one by taking the tensor product...)
- Next add interactions between transmon and oscillator. We could take the time to derive this step by step from circuit quantization, but here rather accept that the interaction term arising from capacitive coupling takes the form $H_\text{int} = g \hat{n}(\hat{a} + \hat{a}^\dagger)$. We can enter this by using the `.add_interaction` method. Or you can just use the GUI that is brought up by `hspace = scq.HilbertSpace.create()`. Once created, the variable `hspace` then contains the `HilbertSpace` that you define with the GUI.
- Observe that the eigenenergies have now shifted with respect to your earlier output.

*Advanced*:<br>
For this subtask, we want to repeat the simulation from Task 4, but now in a more realistic setup. In most experiments, the transmon is driven via the charge operator *of the cavity*, which is proportional to $\hat{a} + \hat{a}^\dagger$. Because transmon and cavity are coupled via the interaction term you added in the *Basic* section, this drive indirectly acts on the transmon.
- Previously, you  diagonalized the Hamiltonian of the coupled system. This yields the dressed eigenstates which differ from the bare eigenstates and their tensor products. (Note: keep the truncation levels the same as the dimension of the Hilbertspace, i.e., `dressed_evals, dressed_evecs = hspace.eigensys(evals_count = 36)`. [This is not a recommendation but a requirement to preserve Qobj compatibility.]) However, in the dispersive regime, the two sets of states are quite similar and the modifications are only small (but important). To establish a mapping between bare product states and corresponding dressed eigenstates, `scqubits` provides a lookup table, which must be generated by calling the function `hspace.generate_lookup()`. The bare and dressed indices can then be interconverted by methods like `hspace.dressed_index((1,0))` or `hspace.bare_index(2)`. Try this!
- Moving forward, there are two paths that you can choose from: (1) represent operators in the product basis of bare eigenstates (not true eigenstates of the coupled system), or (2) represent everything in terms of the dressed (true) eigenstates of the system. (Note that these two methods are may require different truncation levels.)
- First, we output the Hamiltonian of this composite system as a `Qobj` variable defined in `QuTiP`. For path (1), this is by `H_sys = hspace.hamiltonian()`
; for path (2), you can manually define a `Qobj` Hamiltonian `H_sys = q.Qobj(np.diag(dressed_evals))`.
- Second, we output the cavity annihilation operator as a `Qobj` variable as well. For both paths, you can use helper functions provided by `scqubits`. For (1), define the annihilation operator as `a_r = scq.identity_wrap(res.annihilation_operator(), res, hspace.subsystem_list)`; For (2), define `a_r = hspace.op_in_dressed_eigenbasis(op=res.annihilation_operator)`. However, there is an incompatibility for (2) in `Qobj.dims` by the manual definition of the Hamiltonian. To fix this, you can manually set `a_r.dims = [[len(dressed_evals)],[len(dressed_evals)]]`.
- Third, we define the initial state for the simulation of system-state evolution in the next step. This state is chosen as the dressed (true) ground state of this composite system. For (1), we define `zero_state = dressed_evecs[hspace.dressed_index((0,0))]`. For (2), this is simply the 0th state of this basis, which is `zero_state = q.basis(len(dressed_evals), 0)`.
- The fourth step is analogous to what you did in task 4. Note that the target state for (1) is `one_state = dressed_evecs[hspace.dressed_index((1,0))]` and for (2) is `one_state = q.basis(len(dressed_evals), hspace.dressed_index((1,0)))`.
- Finally, you can repeat what was done in Task 4. But a stronger drive `A` is needed for similar gate duration since this drive only indirectly acts on the qubit drive in this case.


Import all relevant packages

In [5]:
import scqubits as scq
import qutip as q
import numpy as np
import matplotlib.pyplot as plt